In [201]:
import pandas as pd
import altair as alt
import numpy as np
import scipy
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [421]:
raw_data_hr = pd.read_json('data_dump_spo2.json', orient='index')
raw_data_hr = raw_data_hr.loc[(raw_data_hr['ir'] != 0) & (raw_data_hr['red'] != 0)].reset_index(drop=True).reset_index()
#aw_data_hr.rename(columns={'raw_readings_ir':'ir', 'raw_readings_red':'red'}, inplace=True)
#raw_data_hr = raw_data_hr.loc[(raw_data_hr['ir'] > 50000) & (raw_data_hr['red'] != 0)].reset_index(drop=True).reset_index()
#raw_data_hr = raw_data_hr.loc[raw_data_hr.index<5000]
raw_data_hr #[['raw_readings_ir','raw_readings_red']]

index    result_red      mean_red           w_ir  \
0         0  11192.000000  11192.000000   21376.000000   
1         1  10640.400000  10916.200000   41739.200000   
2         2  10076.380000  10636.260000   61036.240000   
3         3   9580.561000  10372.335250   79384.428000   
4         4   9117.532950  10121.374790   96823.206600   
...     ...           ...           ...            ...   
4786   4786   -117.743551     22.659636  421805.192439   
4787   4787   -119.856374      7.926655  421450.932817   
4788   4788    -73.863555     -5.269678  421114.386176   
4789   4789    -86.170377    -21.806194  420874.666867   
4790   4790     30.138142    -27.915885  420798.933524   

                         timestamp     result_ir     ir          w_red  \
0    2020-06-27 15:23:55.229223967  21376.000000  21376   11192.000000   
1    2020-06-27 15:23:55.230454922  20363.200000  21432   21832.400000   
2    2020-06-27 15:23:55.231489897  19297.040000  21384   31908.780000   
3    2020-06-27 15:23:55.232511044  18348.188000  21400   41489.341000   
4    2020-06-27 15:23:55.233532906  17438.778600  21408   50606.873950   
...                            ...           ...    ...            ...   
4786 2020-06-27 15:24:50.604386091   -313.957497  20792  257757.127470   
4787 2020-06-27 15:24:50.627526045   -354.259622  20736  257637.271097   
4788 2020-06-27 15:24:50.649194956   -336.546641  20736  257563.407542   
4789 2020-06-27 15:24:50.673023939   -239.719309  20816  257477.237165   
4790 2020-06-27 15:24:50.696610928    -75.733343  20968  257507.375307   

           mean_ir    red  
0     21376.000000  11192  
1     20869.600000  11200  
2     20345.413333  11168  
3     19846.107000  11176  
4     19364.641320  11192  
...            ...    ...  
4786     94.326021  12776  
4787     41.609720  12768  
4788    -11.670766  12808  
4789    -54.287228  12792  
4790    -85.172866  12904  

[4791 rows x 10 columns]

In [480]:
i_rms_red = np.sqrt(raw_data_hr['result_red'].apply(lambda j: j*j).sum()/len(x))
i_rms_ir = np.sqrt(raw_data_hr['result_ir'].apply(lambda j: j*j).sum()/len(x))
R = (i_rms_red * 600) / (i_rms_ir * 900) 

110 -  25 * R

100.85610752123738

In [474]:
b, a = scipy.signal.butter(1, 0.01, 'low', fs=1, output='ba')
raw_data_hr['butterworth_red'] = scipy.signal.filtfilt(b, a, raw_data_hr['result_red'])

data = raw_data_hr[2000:3000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='butterworth_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [440]:
data = raw_data_hr[1000:2000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='result_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [441]:
data = raw_data_hr[1000:2000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='result_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [442]:
data = raw_data_hr[1000:2000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='mean_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [443]:
data = raw_data_hr[1000:2000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='mean_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [422]:
raw_data_hr_melted = raw_data_hr.melt(value_vars=['ir','red'], id_vars='index')
raw_data_hr_melted

index variable  value
0         0       ir  21376
1         1       ir  21432
2         2       ir  21384
3         3       ir  21400
4         4       ir  21408
...     ...      ...    ...
9577   4786      red  12776
9578   4787      red  12768
9579   4788      red  12808
9580   4789      red  12792
9581   4790      red  12904

[9582 rows x 3 columns]

In [ ]:
data = raw_data_hr[1000:2000]
alt.Chart(data).mark_line().encode(
    x='index',
    y='result_ir',
).properties(
    width=1000,
    height=400
)

In [424]:
alt.Chart(raw_data_hr_melted).mark_line().encode(
    x='index',
    y=alt.Y('value:Q',
        scale=alt.Scale(domain=(5000, 35000))
    ),
    color='variable'
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [425]:
class dcFilter_t:
    def __init__(self):
        self.w = None
        self.result = None

def dc_filter(x, alpha=0.95):
    print(x.ir, x.name)
    if x.name ==0:
        prev_w = 0
    filtered = {'w':None, 'result': None}
    filtered['w'] = x.ir + alpha * prev_w ;
    filtered['result'] = filtered['w'] - prev_w;
    return filtered



In [426]:
def _wR(i, col):
    x_i = raw_data_hr_melted.loc[raw_data_hr_melted['variable'] == col, 'value'].loc[i]
    if i==0:
        return x_i
    return x_i + _wR(i-1, col)

def _w(x, col): 
    return _wR(int(x.name), col)

In [427]:
_filtered = {}

for i in raw_data_hr.index:
    _filtered[i] = {}
    if i==0:
        _filtered[i]['w_ir'] = raw_data_hr.loc[i, 'ir']
        _filtered[i]['result_ir'] = _filtered[i]['w_ir']
    else:
        _filtered[i]['w_ir'] = raw_data_hr.loc[i, 'ir'] + 0.95 * _filtered[i-1]['w_ir']
        _filtered[i]['result_ir'] = _filtered[i]['w_ir'] - _filtered[i-1]['w_ir']
        
for i in raw_data_hr.index:
    if i==0:
        _filtered[i]['w_red'] = raw_data_hr.loc[i, 'red']
        _filtered[i]['result_red'] = _filtered[i]['w_red']
    else:
        _filtered[i]['w_red'] = raw_data_hr.loc[i, 'red'] + 0.95 * _filtered[i-1]['w_red']
        _filtered[i]['result_red'] = _filtered[i]['w_red'] - _filtered[i-1]['w_red']

In [428]:
_filtered

{0: {'w_ir': 21376, 'result_ir': 21376, 'w_red': 11192, 'result_red': 11192},
 1: {'w_ir': 41739.2,
  'result_ir': 20363.199999999997,
  'w_red': 21832.4,
  'result_red': 10640.400000000001},
 2: {'w_ir': 61036.24,
  'result_ir': 19297.04,
  'w_red': 31908.78,
  'result_red': 10076.379999999997},
 3: {'w_ir': 79384.42799999999,
  'result_ir': 18348.187999999987,
  'w_red': 41489.341,
  'result_red': 9580.561000000002},
 4: {'w_ir': 96823.20659999998,
  'result_ir': 17438.77859999999,
  'w_red': 50606.87395,
  'result_red': 9117.53295},
 5: {'w_ir': 113422.04626999998,
  'result_ir': 16598.83967,
  'w_red': 59276.5302525,
  'result_red': 8669.6563025},
 6: {'w_ir': 129190.94395649998,
  'result_ir': 15768.8976865,
  'w_red': 67536.703739875,
  'result_red': 8260.173487374996},
 7: {'w_ir': 144163.396758675,
  'result_ir': 14972.452802175016,
  'w_red': 75391.86855288123,
  'result_red': 7855.164813006239},
 8: {'w_ir': 158395.22692074123,
  'result_ir': 14231.830162066239,
  'w_red': 82

In [429]:
filtered = pd.DataFrame(_filtered).transpose()
filtered = filtered.loc[(filtered.index>500) ].reset_index(drop=True).reset_index()
filtered['median_filter_ir'] = scipy.signal.medfilt(filtered['result_ir'], 9)
#butter
b, a = scipy.signal.butter(1, 10/100, 'low', fs=100, output='ba')
filtered['butterworth_red'] = scipy.signal.filtfilt(b, a, filtered['result_red'])
filtered

index           w_ir   result_ir          w_red  result_red  \
0         0  445965.778665   64.959018  280021.204217   32.568199   
1         1  446027.489731   61.711067  280052.144006   30.939789   
2         2  446086.115245   58.625513  280081.536806   29.392800   
3         3  446837.809482  751.694238  280365.459966  283.923160   
4         4  446943.919008  106.109526  280427.186967   61.727002   
...     ...            ...         ...            ...         ...   
4285   4285  421805.192439 -313.957497  257757.127470 -117.743551   
4286   4286  421450.932817 -354.259622  257637.271097 -119.856374   
4287   4287  421114.386176 -336.546641  257563.407542  -73.863555   
4288   4288  420874.666867 -239.719309  257477.237165  -86.170377   
4289   4289  420798.933524  -75.733343  257507.375307   30.138142   

      median_filter_ir  butterworth_red  
0            58.625513        15.246632  
1            61.711067        15.289600  
2            64.959018        15.331949  
3            90.975655        15.371216  
4            90.975655        15.404586  
...                ...              ...  
4285       -195.744733        -5.766814  
4286       -195.744733        -5.743169  
4287       -195.744733        -5.715494  
4288       -195.744733        -5.684553  
4289        -75.733343        -5.651705  

[4290 rows x 7 columns]

In [430]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='result_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [431]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='result_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [432]:
alt.Chart(filtered.loc[(filtered.index>540) & (filtered.index<2380)]).mark_line().encode(
    x='index',
    y='median_filter_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [433]:
x = filtered.loc[(filtered.index>540) & (filtered.index<2380)]
x

index           w_ir   result_ir          w_red  result_red  \
541     541  455840.410106   58.925784  282106.429324   -1.391017   
542     542  455896.389601   55.979495  282105.107858   -1.321466   
543     543  455949.570121   53.180520  282103.852465   -1.255393   
544     544  456112.091615  162.521494  282126.659842   22.807377   
545     545  456162.487034   50.395419  282140.326850   13.667008   
...     ...            ...         ...            ...         ...   
2375   2375  433850.096398  155.258084  269466.516970   40.709633   
2376   2376  433813.591578  -36.504820  269441.191122  -25.325849   
2377   2377  433786.911999  -26.679579  269433.131565   -8.059556   
2378   2378  433769.566399  -17.345600  269433.474987    0.343422   
2379   2379  433785.088079   15.521680  269433.801238    0.326251   

      median_filter_ir  butterworth_red  
541          55.979495        -6.996068  
542          55.979495        -7.007888  
543          55.979495        -7.019933  
544          55.979495        -7.032443  
545          53.180520        -7.045803  
...                ...              ...  
2375        -14.118466        -6.597716  
2376        -13.412543        -6.612406  
2377        -14.118466        -6.627180  
2378        -13.412543        -6.641810  
2379         14.745596        -6.656632  

[1839 rows x 7 columns]

0.23462436239284046

SyntaxError: invalid syntax (<ipython-input-436-af13a54b8cff>, line 1)

In [437]:
filtered.loc[(filtered.index>540) & (filtered.index<2380)]

index           w_ir   result_ir          w_red  result_red  \
541     541  455840.410106   58.925784  282106.429324   -1.391017   
542     542  455896.389601   55.979495  282105.107858   -1.321466   
543     543  455949.570121   53.180520  282103.852465   -1.255393   
544     544  456112.091615  162.521494  282126.659842   22.807377   
545     545  456162.487034   50.395419  282140.326850   13.667008   
...     ...            ...         ...            ...         ...   
2375   2375  433850.096398  155.258084  269466.516970   40.709633   
2376   2376  433813.591578  -36.504820  269441.191122  -25.325849   
2377   2377  433786.911999  -26.679579  269433.131565   -8.059556   
2378   2378  433769.566399  -17.345600  269433.474987    0.343422   
2379   2379  433785.088079   15.521680  269433.801238    0.326251   

      median_filter_ir  butterworth_red  
541          55.979495        -6.996068  
542          55.979495        -7.007888  
543          55.979495        -7.019933  
544          55.979495        -7.032443  
545          53.180520        -7.045803  
...                ...              ...  
2375        -14.118466        -6.597716  
2376        -13.412543        -6.612406  
2377        -14.118466        -6.627180  
2378        -13.412543        -6.641810  
2379         14.745596        -6.656632  

[1839 rows x 7 columns]

In [438]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='butterworth_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [376]:
data = {
    0: {'v1': 21312,'v2':33223},
    1: {'v1': 21312,'v2':33223},
    2: {'v1': 21312,'v2':33223},
    3: {'v1': 21312,'v2':33223},
    4: {'v1': 21312,'v2':33223},
    5: {'v1': 21312,'v2':33223},
    6: {'v1': 21312,'v2':33223},
}

In [377]:
[v for k,v in data.items()]

[{'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223},
 {'v1': 21312, 'v2': 33223}]

In [405]:
def get_last_k_readings(data, var, kernel_size):
    x = list(data.items())
    x.reverse()
    return np.array([v[var] for i, v in x if i > len(x) - kernel_size - 1])

In [409]:
data = {
    0: {'v1': 21312,'v2':33223},
}

In [410]:
get_last_k_readings(data, 'v1', 10)

array([21312])

In [450]:
scipy.signal.butter(1, 7.5/100, 'low', fs=100, output='ba')

(array([0.00235066, 0.00235066]), array([ 1.        , -0.99529868]))